In [1]:
import numpy as np
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt
import os.path
from bs4 import BeautifulSoup
import requests

In [2]:
first_record = 17000
last_record = 22317
record_segment_file_name = '../../../2_data/' + 'record_segment_good_length_' + str(first_record) + '_' + str(last_record - 1) +'.csv'

In [3]:
record_segment_file_name

'../../../2_data/record_segment_good_length_17000_22316.csv'

In [4]:
record_path_local = '../../../2_data/record_path_mimic3_matched.csv'
record_root_url = 'https://physionet.org/content/mimic3wdb/1.0/matched'
record_path_url = record_root_url + '/RECORDS-waveforms'

signal_extract_name = 'PLETH'
sampling_frequency = 125 # Hz
signal_extract_minimum_length = 5 # the minimum length of the signal segment, in minutes

print('record_path_local: {}'.format(record_path_local))
print('record_root_url: {}'.format(record_root_url))
print('record_path_url: {}'.format(record_path_url))

record_path_local: ../../../2_data/record_path_mimic3_matched.csv
record_root_url: https://physionet.org/content/mimic3wdb/1.0/matched
record_path_url: https://physionet.org/content/mimic3wdb/1.0/matched/RECORDS-waveforms


In [5]:
def get_url_content(url, tag=None):
    
    '''
    This function scrapes a list of useful information from a given PhysioNet URL.
    If the URL address points to an HTML document, the information to be extracted is define by a tag.
    I found this address (https://hackersandslackers.com/scraping-urls-with-beautifulsoup/) usefull
      for details on how to scrape a web page
    '''
    
    headers = {
        'Access-Control-Allow-Origin': '*',
        'Access-Control-Allow-Methods': 'GET',
        'Access-Control-Allow-Headers': 'Content-Type',
        'Access-Control-Max-Age': '3600',
        'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:52.0) Gecko/20100101 Firefox/52.0'
    }    
    
    req = requests.get(url, headers)
    soup = BeautifulSoup(req.content, 'html.parser')
    if '<!DOCTYPE html>' in str(soup):
        content = getattr(soup, str(tag)).getText()
        #content = soup.pre.getText()
    else:
        content = soup.getText()
    return content.splitlines()

In [6]:
def get_signal_name(url_content):
    return [x.split(' ')[-1] for x in url_content[1:]]

In [7]:
tag = 'pre'
record_path_list = get_url_content(record_path_url, tag)
print(len(record_path_list))
for i in range(5):
    print('record_path: {}'.format(record_path_list[i]))

22317
record_path: p00/p000020/p000020-2183-04-28-17-47
record_path: p00/p000030/p000030-2172-10-16-12-22
record_path: p00/p000033/p000033-2116-12-24-12-35
record_path: p00/p000033/p000033-2116-12-25-13-11
record_path: p00/p000052/p000052-2191-01-10-02-21


In [8]:
tag = 'pre'
#last_record = len(record_path_list) + 1
for process_record_index in range(first_record, last_record):
        
    #print(process_record_index)
    record_path = record_path_list[process_record_index]
    record_path_short = record_path.split('/')[2]
    print('processing record #: {}, record_path_short: {}'.format(process_record_index, record_path_short))
    
    directory = str(record_path.split("/")[0]) + '/' + str(record_path.split("/")[1])
    #print('directory: {}'.format(directory))
            
    master_waveform_header = record_root_url + '/' + record_path + '.hea'
    #print('master_waveform_header: {}'.format(master_waveform_header))
    
    target_url = master_waveform_header
    master_waveform_content = get_url_content(target_url, tag)
    #print('master_waveform_content: {}'.format(master_waveform_content))
    #print('       ...........\n')
    
    master_waveform_content_first_line = master_waveform_content[0].split(' ')
    record_length = int(master_waveform_content_first_line[3]) / sampling_frequency
    #print('record_length (s): {}'.format(record_length))
    #print('       ...........\n')
        
    waveform_layout_header = master_waveform_content[1].split(' ')[0]
    #print('1. waveform_layout_header: {}\n'.format(waveform_layout_header))
    
    waveform_layout_header = waveform_layout_header + '.hea'
    #print('2. waveform_layout_header: {}\n'.format(waveform_layout_header))
    
    waveform_layout_header = record_root_url + '/' + directory + '/' + waveform_layout_header
    #print('record_root_url: {}'.format(record_root_url))
    #print('directory: {}'.format(directory))
    #print('3. waveform_layout_header: {}\n'.format(waveform_layout_header))
    #print('waveform_layout_header: {}\n'.format(waveform_layout_header))
    
    target_url = waveform_layout_header
    waveform_layout_content = get_url_content(target_url, tag)
    #print('waveform_layout_content: {}'.format(waveform_layout_content))
        
    record_signal_names = get_signal_name(waveform_layout_content)
    #print('record_signal_names: {}'.format(record_signal_names))
    
    if signal_extract_name in record_signal_names and record_length > 60 * signal_extract_minimum_length: # and len(record_segments_path_list):      
        
        # Open the record_segment_file_name file with access mode 'a'
        record_segment_file_object = open(record_segment_file_name, 'a')

        # get the waveform record name
        waveform_record_id = [x.split(' ')[0].split('_') for x in master_waveform_content if '3' == x[0]][0][0]
        #print('waveform_record_id: {}\n'.format(waveform_record_id))
        
        # get the waveform_record_state
        waveform_record_state = [(waveform_record_id + '_' in x) and not (waveform_record_id + '_layout' in x) 
                for x in master_waveform_content]
        #print('waveform_record_state: {}\n'.format(waveform_record_state))

        # get the waveform_record_segment
        waveform_record_segment = [master_waveform_content[x].split(' ') for x, y in enumerate(waveform_record_state) if y]
        #print('waveform_record_segment: {}\n'.format(waveform_record_segment))
      
        for segment_index in range(len(waveform_record_segment)):
            # number of samples: int(waveform_record_segment[segment_index][1])
            # sampling frequency: int(master_waveform_content_first_line[2])
            # length (in seconds) of the record segment: number of samples / sampling frequency
            
            # https://physionet.org/content/mimic3wdb/1.0/matched/p00/p000107/3168852_0001.hea
            
            segment_header = record_root_url + '/' + directory + '/' + waveform_record_segment[segment_index][0] + '.hea'
            #print(segment_header)
            
            segment_header_content = get_url_content(segment_header, tag)
            #print('segment_header_content: {}\n'.format(segment_header_content))
            
            segment_signal_names = get_signal_name(segment_header_content)
            #print('segment_signal_names: {}\n'.format(segment_signal_names))
           
            waveform_record_segment_length = int(waveform_record_segment[segment_index][1]) / sampling_frequency
            #print('waveform_record_segment_length: {}\n'.format(waveform_record_segment_length))
            
            if signal_extract_name in segment_signal_names and waveform_record_segment_length > 60 * signal_extract_minimum_length:
                
                waveform_record_segment_good_length = waveform_record_segment[segment_index][0]
                print('  ' + str(process_record_index) + ',' + record_path + ',' + waveform_record_segment_good_length)                
                
                # Append the waveform_record_segment_good_length_root at the end of file record_segment_file_name
                record_segment_file_object.write(str(process_record_index) + ',' + record_path + ',' + waveform_record_segment_good_length + '\n')
        
        # Close the file record_segment_file_name
        record_segment_file_object.close()
        
    #index_of_last_record_processed = index_of_last_record_processed + 1
    print('  \nindex of last record processed successfully: {}'.format(process_record_index))  
    print('--------------------------------------')

    
    


processing record #: 17000, record_path_short: p077697-2107-07-26-20-06
  17000,p07/p077697/p077697-2107-07-26-20-06,3792554_0002
  17000,p07/p077697/p077697-2107-07-26-20-06,3792554_0004
  17000,p07/p077697/p077697-2107-07-26-20-06,3792554_0010
  17000,p07/p077697/p077697-2107-07-26-20-06,3792554_0012
  
index of last record processed successfully: 17000
--------------------------------------
processing record #: 17001, record_path_short: p077697-2107-07-28-19-01
  17001,p07/p077697/p077697-2107-07-28-19-01,3273137_0006
  17001,p07/p077697/p077697-2107-07-28-19-01,3273137_0010
  17001,p07/p077697/p077697-2107-07-28-19-01,3273137_0013
  17001,p07/p077697/p077697-2107-07-28-19-01,3273137_0016
  
index of last record processed successfully: 17001
--------------------------------------
processing record #: 17002, record_path_short: p077702-2154-07-26-20-06
  
index of last record processed successfully: 17002
--------------------------------------
processing record #: 17003, record_path_s

  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0003
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0004
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0006
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0008
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0009
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0011
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0013
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0015
  17027,p07/p077805/p077805-2115-07-22-16-55,3713664_0017
  
index of last record processed successfully: 17027
--------------------------------------
processing record #: 17028, record_path_short: p077807-2125-08-18-00-21
  17028,p07/p077807/p077807-2125-08-18-00-21,3209787_0002
  17028,p07/p077807/p077807-2125-08-18-00-21,3209787_0004
  17028,p07/p077807/p077807-2125-08-18-00-21,3209787_0006
  17028,p07/p077807/p077807-2125-08-18-00-21,3209787_0008
  17028,p07/p077807/p077807-2125-08-18-00-21,3209787_0011
  17028,p07/p077807/p07

  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0024
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0027
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0028
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0030
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0032
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0034
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0036
  17034,p07/p077815/p077815-2166-11-07-16-59,3258704_0038
  
index of last record processed successfully: 17034
--------------------------------------
processing record #: 17035, record_path_short: p077826-2181-08-21-11-14
  17035,p07/p077826/p077826-2181-08-21-11-14,3963345_0010
  17035,p07/p077826/p077826-2181-08-21-11-14,3963345_0011
  17035,p07/p077826/p077826-2181-08-21-11-14,3963345_0012
  
index of last record processed successfully: 17035
--------------------------------------
processing record #: 17036, record_path_short: p077826-2181-08-22-17-06
  17036,p07/p077826/p077826-2181

  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0001
  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0003
  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0006
  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0009
  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0014
  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0019
  17052,p07/p077850/p077850-2158-07-30-13-06,3193389_0023
  
index of last record processed successfully: 17052
--------------------------------------
processing record #: 17053, record_path_short: p077873-2157-05-08-06-35
  
index of last record processed successfully: 17053
--------------------------------------
processing record #: 17054, record_path_short: p077873-2157-05-24-13-44
  17054,p07/p077873/p077873-2157-05-24-13-44,3589389_0014
  17054,p07/p077873/p077873-2157-05-24-13-44,3589389_0018
  17054,p07/p077873/p077873-2157-05-24-13-44,3589389_0020
  17054,p07/p077873/p077873-2157-05-24-13-44,3589389_0022
  
index of last record processe

  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0180
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0181
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0184
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0187
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0190
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0193
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0196
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0199
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0202
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0205
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0208
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0211
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0214
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0217
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0220
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0223
  17058,p07/p077927/p077927-2151-01-06-21-53,3592752_0226
  17058,p07/p0

...

  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0002
  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0006
  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0008
  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0010
  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0012
  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0014
  22245,p09/p099752/p099752-2138-07-17-14-11,3035645_0019
  
index of last record processed successfully: 22245
--------------------------------------
processing record #: 22246, record_path_short: p099756-2191-08-03-20-02
  
index of last record processed successfully: 22246
--------------------------------------
processing record #: 22247, record_path_short: p099756-2191-12-23-02-00
  
index of last record processed successfully: 22247
--------------------------------------
processing record #: 22248, record_path_short: p099759-2161-03-10-16-38
  
index of last record processed successfully: 22248
--------------------------------------
proces

  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0042
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0044
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0046
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0048
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0049
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0050
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0051
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0052
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0053
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0057
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0058
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0060
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0062
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0068
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0072
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0076
  22267,p09/p099785/p099785-2122-10-10-04-21,3995417_0078
  22267,p09/p0

  22280,p09/p099836/p099836-2116-06-25-22-21,3126408_0041
  22280,p09/p099836/p099836-2116-06-25-22-21,3126408_0044
  22280,p09/p099836/p099836-2116-06-25-22-21,3126408_0045
  22280,p09/p099836/p099836-2116-06-25-22-21,3126408_0049
  
index of last record processed successfully: 22280
--------------------------------------
processing record #: 22281, record_path_short: p099836-2116-06-27-12-31
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0005
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0008
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0011
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0014
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0017
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0018
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0019
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0022
  22281,p09/p099836/p099836-2116-06-27-12-31,3899730_0027
  
index of last record processed successfully: 22281
---------------------------

  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0006
  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0009
  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0012
  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0013
  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0016
  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0019
  22287,p09/p099863/p099863-2142-04-06-18-42,3883931_0021
  
index of last record processed successfully: 22287
--------------------------------------
processing record #: 22288, record_path_short: p099863-2142-04-11-07-59
  
index of last record processed successfully: 22288
--------------------------------------
processing record #: 22289, record_path_short: p099863-2142-04-16-17-54
  
index of last record processed successfully: 22289
--------------------------------------
processing record #: 22290, record_path_short: p099865-2184-12-23-14-53
  22290,p09/p099865/p099865-2184-12-23-14-53,3938446_0001
  22290,p09/p099865/p099865-2184-12-23-14

  
index of last record processed successfully: 22301
--------------------------------------
processing record #: 22302, record_path_short: p099913-2141-05-12-13-30
  
index of last record processed successfully: 22302
--------------------------------------
processing record #: 22303, record_path_short: p099922-2107-04-07-12-17
  
index of last record processed successfully: 22303
--------------------------------------
processing record #: 22304, record_path_short: p099946-2161-07-14-21-47
  22304,p09/p099946/p099946-2161-07-14-21-47,3382559_0008
  22304,p09/p099946/p099946-2161-07-14-21-47,3382559_0010
  22304,p09/p099946/p099946-2161-07-14-21-47,3382559_0012
  22304,p09/p099946/p099946-2161-07-14-21-47,3382559_0015
  22304,p09/p099946/p099946-2161-07-14-21-47,3382559_0017
  
index of last record processed successfully: 22304
--------------------------------------
processing record #: 22305, record_path_short: p099955-2139-07-14-04-45
  22305,p09/p099955/p099955-2139-07-14-04-45,38403